![](ubc_header.png)

# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
****

## Part I: Data Preprocessing

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest

C:\Users\smvan\anaconda3\lib\site-packages\pdpipe\col_generation.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
# Changed the path here, May 2nd 2023
# Set the root path, change the the current working directory into the project folder
path = "C:/Users/smvan/CFFS-S23/CFFS-22-23"
# path = os.getcwd()

# os.chdir is used to change the current directory to the specified path
os.chdir(path)
print(path)

C:/Users/smvan/CFFS-S23/CFFS-22-23


In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

****

## Load Data Files

### Set Data File Path

In [5]:
# Select data file path for the chosen venue and time range where the recipes data stored

# Totem 2019
filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Totem 19-20*", "*.oc"))

# Gather 2019
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Gather 19-20*", "*.oc"))

# OK 2019
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "OK 19-20*", "*.oc"))

# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "OK 22-23*", "*.oc"))
filepath_list

['C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Add Ons.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Bueno and Desserts.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Dim Sum.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Feast.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\FT Mercante.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\FT Oasis Chaat.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\FT Sides Soup.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\FT Sticks and spoons.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\FT SweetGreen Ucare Boxes.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Grab & Go A.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\Grab & Go B.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Totem 19-20\\

### Import Items List

In [6]:
# Read items.xml files in the filepath_list and construct a dataframe
ItemId = []
Description = []
CaseQty = []
CaseUOM = []
PakQty = []
PakUOM = []
InventoryGroup = []


# from the items xml file, findtext of CaseQty, CaseUOM, PakQty, PakUOM, and InventoryGroup
# then append it on the lists above

for filepath in filepath_list:
    path = filepath + '/items.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for item in xtree.iterfind('Item'):
            ItemId.append(item.attrib['id'])
            Description.append(item.findtext('Description'))
            CaseQty.append(item.findtext('CaseQty'))
            CaseUOM.append(item.findtext('CaseUOM'))
            PakQty.append(item.findtext('PakQty'))
            PakUOM.append(item.findtext('PakUOM'))
            InventoryGroup.append(item.findtext('InventoryGroup'))

            
# Create a dataframe from the lists created above.
        
Items = pd.DataFrame({'ItemId': ItemId, 'Description': Description, 'CaseQty': CaseQty, 
                      'CaseUOM': CaseUOM, 'PakQty': PakQty, 'PakUOM': PakUOM, 'InventoryGroup': InventoryGroup}
                    )
Items.drop_duplicates(inplace=True)

Items.reset_index(drop=True, inplace=True)

In [7]:
Items

ItemId                     Description     CaseQty CaseUOM     PakQty  \
0     I-2110       CHEESE CHED MED SHRED COL       2.000     bag      2.500   
1     I-4027       CHICK THIGH B/LS/L HALAL        1.000      Kg      1.000   
2     I-3237     CRACKER SODA SALTED IND TFC     500.000     pak      1.000   
3     I-3388           OIL CANOLA ROMANO TFC       6.000     can      3.000   
4     I-3642       PEPPER BLK COARSE GRD SHK      12.000      ea    500.000   
5     I-6026             SALT KOSHER WINDSOR      16.320      Kg   1000.000   
6    I-43851                      AJWAIN 5LB       5.000      lb    454.000   
7     I-3617         ALLSPICE GROUND SHAKER        8.000    each    454.000   
8    I-43854                   AMCHUR POWDER       5.000      lb    454.000   
9     I-4472                      AVOCADO MX      20.000      CT      1.000   
10    I-4973             AVOCADO PULP CHUNKY      12.000     bag    454.000   
11    I-1252           BAGEL PLAIN  (6 PACK)       6.000      CT      1.000   
12    I-1277       BAGEL SESAME SEED 6 PACK)       6.000      CT      1.000   
13    I-1286      BAGEL WHOLE WHEAT (6 PACK)       6.000      CT      1.000   
14    I-8118                BAGUETTE PARBAKE      16.000    LOAF      1.000   
15    I-4497                BAK CHOY BABY US      30.000      lb      1.000   
16    I-1402          BAR GF NANAIMO COCONUT      24.000      CT      1.000   
17    I-1020     BAR NANAIMO SCORED 12X16IN        2.000   SHEET      1.000   
18   I-55475              BASE CHOCO PREMIUM       1.000   1.6KG      1.600   
19   I-62123          BASE GREEN TEA PREMIUM       1.000   1.6KG      1.600   
20   I-55476            BASE VANILLA PREMIUM       1.000   1.6KG      1.600   
21    I-3619         BAY LEAF WHL SHAKER TFC       8.000    each     84.000   
22    I-2567      BEAN GREEN WHL GRADE A IQF       6.000     bag      1.500   
23   I-42273           BEANS BLACK KOON CHUN      96.000     can      1.000   
24   I-23336                BEANS CANNELLINI       6.000     can      2.840   
25    I-3143       BEANS CHICK PEAS GARBANZO       6.000  LG CAN      2.840   
26    I-4515                    BEANS GREEN        1.000      lb      1.000   
27    I-7935                  BEANS NAVY WHT      10.000      Kg      1.000   
28    I-3148            BEANS TURTLE BLK DRY      10.000      Kg      1.000   
29   I-59287       BEEF GRD MUSH/ONION BLEND       5.000      Kg      1.000   
30    I-3837          BEEF STEW DICED 3/4"FR       1.000      Kg      1.000   
31   I-10869             BEEF STIRFRY COV FR       5.000      Kg      1.000   
32   I-19711           BEETS SHREDDED COARSE       5.000      lb      1.000   
33   I-47657         BEYOND MEAT CRUMBLE FZN      10.000      lb      1.000   
34    I-1157     BISCOTTI AMARETTO (15 PACK)      15.000      CT      1.000   
35   I-45976        BISCOTTI LEMON CRANBERRY      15.000      CT      1.000   
36    I-1283  BROWNIE CHOCOLATE TRADITIONAL        6.000      CT      1.000   
37    I-1016  BROWNIE ROCKY ROAD 12X16IN TFC       2.000   SHEET      1.000   
38   I-46907   Brownies-Blackbean Square 6ea       6.000      ea      1.000   
39   I-32395     BS Xmas Gingerbread Peoples       6.000      ea      1.000   
40   I-32394     BS Xmas Mincemeat Tart 6 ea       6.000      ea      1.000   
41   I-32393  BS Xmas Tree\Bell Sugar Cookie       6.000      ea      1.000   
42   I-38808    BS|Cookies|Sugar Pumpkin 6ea       6.000      ea      1.000   
43   I-29427               BS|Muffin| 1 |6ea       1.000    6 pk      6.000   
44   I-29443               BS|Muffin| 2 |6ea       1.000    6 pk      6.000   
45   I-29442               BS|Muffin| 3 |6ea       1.000    6 pk      6.000   
46   I-29441               BS|Muffin| 4 |6ea       1.000    6 pk      1.000   
47   I-29438                BS|Scone| 1 |6ea       1.000    6 pk      6.000   
48   I-29437                BS|Scone| 2 |6ea       1.000    6 pk      6.000   
49   I-29436                BS|Scone| 3 |6ea       1.000

In [8]:
# creates a new array with unique ItemIds
all_id_list = Items["ItemId"].unique()

In [9]:
# None of the items are egg yolk liq
Items.loc[Items["Description"] == "Egg Yolk Liq"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [10]:
# Sumplemental option for egg, vegan option
Items.loc[Items["ItemId"] == "I-68700"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [11]:
# Gives you the list of breads
breadlist = []


# If the items in the Items list is a "LOAF", "SANDWICH", or "BREAD" then we should add it in the breadlist
# We append it onto the breadlist at position row["ItemId"]
for ind, row in Items.iterrows():
    if ("LOAF" or "SANDWICH" "BREAD") in row["Description"]:
        breadlist.append(row["ItemId"])

breadlist

['I-47962', 'I-47963', 'I-11842', 'I-14190', 'I-13004', 'I-1373']

In [12]:
# Based on info below there are 486 rows and 7 columns
Items.shape

(913, 7)

In [13]:
Items.dtypes

ItemId            object
Description       object
CaseQty           object
CaseUOM           object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [14]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Items_List.csv")
Items.to_csv(path, index = False, header = True)

### Import Ingredients List

In [15]:
# Read ingredients.xml files in the filepath_list and construct a dataframe
IngredientId = []
Conversion = []
InvFactor = []
Qty = []
Recipe = []
Uom = []

# Using the Ingredients XML file, we extract attributes containing ingredients, conversion, invFactor, qty, recipe, and uom. 
# Then we append it onto the IngredientId, Coversion, InvFactor, Qty, Recipe, and Uom lists
# Then we create a dataframe using the lists created. 

for filepath in filepath_list:
    path = filepath + '/Ingredients.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Ingredient'):
            IngredientId.append(x.attrib['ingredient'])
            Conversion.append(x.attrib['conversion'])
            InvFactor.append(x.attrib['invFactor'])
            Qty.append(x.attrib['qty'])
            Recipe.append(x.attrib['recipe'])
            Uom.append(x.attrib['uom'])
    
Ingredients = pd.DataFrame({'IngredientId': IngredientId, 'Qty': Qty,'Uom': Uom, 'Conversion': Conversion, 
                      'InvFactor': InvFactor,'Recipe': Recipe}).drop_duplicates()
Ingredients.drop_duplicates(subset=["IngredientId", "Recipe"], inplace=True)

Ingredients.reset_index(drop=True, inplace=True)

In [16]:
Ingredients

IngredientId       Qty     Uom     Conversion  InvFactor   Recipe
0          I-3388   150.000      ml     0.00100000    75.0000  P-41914
1          I-3642     5.000       g     1.00000000     2.5000  P-41914
2          I-4027     2.000      Kg     1.00000000     1.0000  P-41914
3          I-6026    20.000       g     1.00000000    10.0000  P-41914
4          I-3237     1.000     pak     1.00000000     1.0000  R-22896
5         P-41914   170.000       g     0.00100000     1.0000  R-53006
6          I-2110    25.000       g     0.00100000     1.0000  R-55408
7          I-3388     1.000       L     1.00000000     0.3058  P-10496
8          I-4660     2.270      Kg     2.20462000     0.6942  P-10496
9          I-1821     1.000       L  1000.00000000     0.0286  P-10874
10         I-3458     2.840       L     1.00000000     0.0811  P-10874
11         I-3511     5.680       L     1.00000000     0.1623  P-10874
12         I-3698     1.000       L     1.00000000     0.0286  P-10874
13         I-4657   250.000       g     0.00220462     7.1429  P-10874
14         I-4660   250.000       g     0.00220462     7.1429  P-10874
15         I-5983    12.000       L     1.00000000     0.3429  P-10874
16         I-6028   300.000       g     0.00100000     8.5714  P-10874
17         I-6820   450.000       g     0.00100000    12.8571  P-10874
18        P-18746     2.500      Kg     1.00000000     0.0714  P-10874
19        P-41094     2.500      Kg     1.00000000     0.0714  P-10874
20        P-41095     2.500      Kg     1.00000000     0.0714  P-10874
21        P-50552     6.000      Kg     2.20462000     0.1714  P-10874
22        I-11842     2.000    LOAF     1.00000000     0.8818  P-13648
23         I-3388   125.000      ml     0.00100000    55.1146  P-13648
24         I-3642     5.000       g     1.00000000     2.2046  P-13648
25         I-6026     5.000       g     1.00000000     2.2046  P-13648
26         I-1813    10.000      ml     0.03381406     4.0000  P-13683
27         I-2156   100.000       g     0.00100000    40.0000  P-13683
28         I-3243   200.000       g     0.00220462    80.0000  P-13683
29         I-3348   500.000      ml     0.00100000   200.0000  P-13683
30         I-3368    60.000      ml     1.00000000    24.0000  P-13683
31         I-3388   120.000      ml     0.00100000    48.0000  P-13683
32         I-3563     5.000      ml     1.00000000     2.0000  P-13683
33         I-3572     5.000      ml     0.00100000     2.0000  P-13683
34         I-4601   200.000       g     0.00220462    80.0000  P-13683
35         I-4741   200.000       g     0.00220462    80.0000  P-13683
36         I-5077     1.000      Kg     2.20462000     0.4000  P-13683
37        P-25993     1.000       g     1.00000000     0.4000  P-13683
38        P-50837   200.000       g     1.00000000    80.0000  P-13683
39         I-4793    10.000      Kg     2.20462000     1.2048  P-18746
40         I-3643   225.000       g     0.00100000     0.1837  P-18907
41         I-6026  1000.000       g     1.00000000     0.8163  P-18907
42         I-6807     2.270      Kg     2.20462000     1.4188  P-19175
43         I-4698    10.000      Kg     4.00000000     1.3514  P-20239
44         I-4626    10.000      CT     1.00000000     2.6316  P-21077
45        I-11804     0.042   SHEET     1.00000000     0.0420  P-22028
46         I-1020     0.042   SHEET     1.00000000     0.0420  P-22029
47         I-1048     1.000   slice     1.00000000     1.0000  P-22030
48         I-1050     1.000      CT     1.00000000     1.0000  P-22031
49         I-1016     0.042   SHEET     1.00000000     0.0420  P-22032
50         I-1062     0.033   SHEET     1.00000000     0.0330  P-22034
51        I-12439    81.250       g     0.00100000    81.2500  P-22035
52         I-5983     1.000       L     1.00000000     1.0000  P-22036
53        I-11824     0.042   SHEET     1.00000000     0.0420  P-22037
54        I-16216    72.000       g     0.00100000    72.0000  P-22040
55         I-5983     1.000  

In [17]:
# .loc attribute is used to filter rows and columns in a DataFrame based on if IngredientId is equal to I-29389

# This information tells us whether or not multiple recipes are using the same ingredient or not. Here we can see that 
# there are 3 recipes that use the same ingredient
Ingredients.loc[Ingredients["IngredientId"] == "I-29389"]

IngredientId    Qty Uom  Conversion InvFactor   Recipe
2547      I-29389  2.260  Kg  1.00000000    1.0273  P-26022

In [18]:
# Create a new dataframe that takes the IngredientId and Recipe column from the Ingredients dataframe

Ingredients_sample = Ingredients[["IngredientId", "Recipe"]]
Ingredients_sample

IngredientId   Recipe
0          I-3388  P-41914
1          I-3642  P-41914
2          I-4027  P-41914
3          I-6026  P-41914
4          I-3237  R-22896
5         P-41914  R-53006
6          I-2110  R-55408
7          I-3388  P-10496
8          I-4660  P-10496
9          I-1821  P-10874
10         I-3458  P-10874
11         I-3511  P-10874
12         I-3698  P-10874
13         I-4657  P-10874
14         I-4660  P-10874
15         I-5983  P-10874
16         I-6028  P-10874
17         I-6820  P-10874
18        P-18746  P-10874
19        P-41094  P-10874
20        P-41095  P-10874
21        P-50552  P-10874
22        I-11842  P-13648
23         I-3388  P-13648
24         I-3642  P-13648
25         I-6026  P-13648
26         I-1813  P-13683
27         I-2156  P-13683
28         I-3243  P-13683
29         I-3348  P-13683
30         I-3368  P-13683
31         I-3388  P-13683
32         I-3563  P-13683
33         I-3572  P-13683
34         I-4601  P-13683
35         I-4741  P-13683
36         I-5077  P-13683
37        P-25993  P-13683
38        P-50837  P-13683
39         I-4793  P-18746
40         I-3643  P-18907
41         I-6026  P-18907
42         I-6807  P-19175
43         I-4698  P-20239
44         I-4626  P-21077
45        I-11804  P-22028
46         I-1020  P-22029
47         I-1048  P-22030
48         I-1050  P-22031
49         I-1016  P-22032
50         I-1062  P-22034
51        I-12439  P-22035
52         I-5983  P-22036
53        I-11824  P-22037
54        I-16216  P-22040
55         I-5983  P-22041
56         I-1064  P-22042
57         I-1073  P-22043
58         I-5983  P-22044
59         I-1059  P-22045
60         I-1060  P-22046
61         I-1061  P-22047
62         I-1065  P-22049
63         I-2596  P-22050
64         I-2661  P-22051
65         I-2662  P-22052
66         I-2664  P-22054
67         I-2667  P-22057
68         I-2668  P-22058
69         I-2669  P-22059
70         I-2671  P-22060
71         I-3329  P-22308
72         I-3330  P-22308
73         I-3333  P-22308
74         I-3334  P-22308
75         I-3335  P-22308
76         I-5983  P-22308
77         I-4695  P-22534
78        I-19633  P-23837
79         I-5983  P-23837
80         I-6850  P-23837
81         I-4793  P-24451
82         I-4381  P-24452
83        P-26514  P-24750
84         I-3642  P-25993
85         I-6026  P-25993
86         I-3388  P-26020
87         I-4657  P-26020
88         I-2897  P-26054
89         I-3348  P-26054
90         I-3572  P-26054
91         I-3695  P-26054
92         I-5983  P-26054
93        P-25993  P-26054
94        P-26020  P-26054
95         I-6443  P-26062
96        P-18907  P-26062
97        P-24750  P-26062
98        P-44429  P-26062
99        P-56811  P-26062
100       P-57499  P-26062
101       I-36672  P-26090
102        I-5983  P-26090
103       P-41468  P-26136
104       P-50547  P-26136
105        I-4341  P-26514
106        I-3388  P-26626
107        I-4657  P-26626
108        I-2911  P-26636
109        I-4695  P-26636
110        I-6026  P-26636
111        I-8060  P-26636
112       P-26626  P-26636
113        I-3388  P-26647
114        I-3416  P-26647
115        I-5983  P-26647
116        I-6026  P-26647
117        I-3589  P-26682
118        I-3591  P-26682
119        I-3857  P-26683
120       P-10874  P-26683
121       P-26682  P-26683
122       P-48933  P-26683
123        I-4679  P-26684
124       P-10874  P-26684
125       P-26682  P-26684
126       P-44851  P-26684
127        I-3477  P-26884
128        I-5983  P-26884
129        I-6026  P-26884
130       I-19295  P-26959
131        I-3392  P-26959
132        I-6443  P-26959
133       P-25993  P-26959
134        I-3370  P-27397
135        I-3388  P-27397
136        I-3451  P-27397
137        I-3620  P-27397
138        I-3624  P-27397
139        I-3625  P-27397
140        I-3628  P-27397
141        I-3630  P-27397
142        I-3660  P-27397
143        I-3695  P-27397
144       I-42230  P-27397
145        I-4657  P-27397
146        I-4660  P-27397
147      

In [19]:
# This will output the IngredientId on the right side and the number of times the ingredient appears in the Ingredients
# dataframe on the left side. 

# The duplicated() method returns a Series with True and False values that describe which rows in the DataFrame are 
# duplicated and not.

check = Ingredients["IngredientId"].duplicated()

# The line below tells us at which index is the ingredient duplicated. For example I-4598 exists on index 2 of the dataframe and
# then again on index 8. So duplicate is first true on index 8, which is why it is printed below. It also appears in a below 
# index so it is printed again with that index number. 
Ingredients["IngredientId"][check]

7        I-3388
14       I-4660
23       I-3388
24       I-3642
25       I-6026
31       I-3388
41       I-6026
52       I-5983
55       I-5983
58       I-5983
76       I-5983
79       I-5983
81       I-4793
84       I-3642
85       I-6026
86       I-3388
87       I-4657
89       I-3348
90       I-3572
92       I-5983
93      P-25993
102      I-5983
106      I-3388
107      I-4657
109      I-4695
110      I-6026
113      I-3388
115      I-5983
116      I-6026
124     P-10874
125     P-26682
128      I-5983
129      I-6026
132      I-6443
133     P-25993
135      I-3388
143      I-3695
145      I-4657
146      I-4660
147      I-5983
150      I-1813
153      I-5983
154      I-6026
155     P-26020
157      I-3392
158      I-3458
162     P-48933
165      I-5983
166      I-8060
177     I-47774
187      I-3696
188      I-4341
190      I-4660
191     I-47774
193      I-5983
194      I-6026
195      I-6028
196     P-50552
200      I-3629
201      I-3642
202      I-3660
203      I-4657
204     

In [20]:
# We can see from the printed items above that I-64877 does not appear because it does not get duplicated
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [21]:
210 * 9.8315

2064.6150000000002

In [22]:
Ingredients

IngredientId       Qty     Uom     Conversion  InvFactor   Recipe
0          I-3388   150.000      ml     0.00100000    75.0000  P-41914
1          I-3642     5.000       g     1.00000000     2.5000  P-41914
2          I-4027     2.000      Kg     1.00000000     1.0000  P-41914
3          I-6026    20.000       g     1.00000000    10.0000  P-41914
4          I-3237     1.000     pak     1.00000000     1.0000  R-22896
5         P-41914   170.000       g     0.00100000     1.0000  R-53006
6          I-2110    25.000       g     0.00100000     1.0000  R-55408
7          I-3388     1.000       L     1.00000000     0.3058  P-10496
8          I-4660     2.270      Kg     2.20462000     0.6942  P-10496
9          I-1821     1.000       L  1000.00000000     0.0286  P-10874
10         I-3458     2.840       L     1.00000000     0.0811  P-10874
11         I-3511     5.680       L     1.00000000     0.1623  P-10874
12         I-3698     1.000       L     1.00000000     0.0286  P-10874
13         I-4657   250.000       g     0.00220462     7.1429  P-10874
14         I-4660   250.000       g     0.00220462     7.1429  P-10874
15         I-5983    12.000       L     1.00000000     0.3429  P-10874
16         I-6028   300.000       g     0.00100000     8.5714  P-10874
17         I-6820   450.000       g     0.00100000    12.8571  P-10874
18        P-18746     2.500      Kg     1.00000000     0.0714  P-10874
19        P-41094     2.500      Kg     1.00000000     0.0714  P-10874
20        P-41095     2.500      Kg     1.00000000     0.0714  P-10874
21        P-50552     6.000      Kg     2.20462000     0.1714  P-10874
22        I-11842     2.000    LOAF     1.00000000     0.8818  P-13648
23         I-3388   125.000      ml     0.00100000    55.1146  P-13648
24         I-3642     5.000       g     1.00000000     2.2046  P-13648
25         I-6026     5.000       g     1.00000000     2.2046  P-13648
26         I-1813    10.000      ml     0.03381406     4.0000  P-13683
27         I-2156   100.000       g     0.00100000    40.0000  P-13683
28         I-3243   200.000       g     0.00220462    80.0000  P-13683
29         I-3348   500.000      ml     0.00100000   200.0000  P-13683
30         I-3368    60.000      ml     1.00000000    24.0000  P-13683
31         I-3388   120.000      ml     0.00100000    48.0000  P-13683
32         I-3563     5.000      ml     1.00000000     2.0000  P-13683
33         I-3572     5.000      ml     0.00100000     2.0000  P-13683
34         I-4601   200.000       g     0.00220462    80.0000  P-13683
35         I-4741   200.000       g     0.00220462    80.0000  P-13683
36         I-5077     1.000      Kg     2.20462000     0.4000  P-13683
37        P-25993     1.000       g     1.00000000     0.4000  P-13683
38        P-50837   200.000       g     1.00000000    80.0000  P-13683
39         I-4793    10.000      Kg     2.20462000     1.2048  P-18746
40         I-3643   225.000       g     0.00100000     0.1837  P-18907
41         I-6026  1000.000       g     1.00000000     0.8163  P-18907
42         I-6807     2.270      Kg     2.20462000     1.4188  P-19175
43         I-4698    10.000      Kg     4.00000000     1.3514  P-20239
44         I-4626    10.000      CT     1.00000000     2.6316  P-21077
45        I-11804     0.042   SHEET     1.00000000     0.0420  P-22028
46         I-1020     0.042   SHEET     1.00000000     0.0420  P-22029
47         I-1048     1.000   slice     1.00000000     1.0000  P-22030
48         I-1050     1.000      CT     1.00000000     1.0000  P-22031
49         I-1016     0.042   SHEET     1.00000000     0.0420  P-22032
50         I-1062     0.033   SHEET     1.00000000     0.0330  P-22034
51        I-12439    81.250       g     0.00100000    81.2500  P-22035
52         I-5983     1.000       L     1.00000000     1.0000  P-22036
53        I-11824     0.042   SHEET     1.00000000     0.0420  P-22037
54        I-16216    72.000       g     0.00100000    72.0000  P-22040
55         I-5983     1.000  

In [23]:
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [24]:
# Below we are checking if we can extract an entire recipe. So we can do .loc with the particular recipe id and then 
# print all the data points (ingredientId, Qty, Uom, Conversion, InvFactor) for that recipe. 
Ingredients.loc[Ingredients["Recipe"] == "R-68698"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [25]:
Items.loc[Items["ItemId"] == "I-68700"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [26]:
Ingredients.shape

(3760, 6)

In [27]:
Ingredients.dtypes

IngredientId    object
Qty             object
Uom             object
Conversion      object
InvFactor       object
Recipe          object
dtype: object

In [28]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Ingredients_List.csv")
Ingredients.to_csv(path, index = False, header = True)

### Import Preps List

In [29]:
# Read preps.xml files in the filepath_list and construct a dataframe
PrepId = []
Description = []
PakQty = []
PakUOM = []
InventoryGroup = []


# Here we do the same thing for the Preps XML file where we find the columns using attrib function and then append it onto
# the dataframe called Preps. 

for filepath in filepath_list:
    path = filepath + '/Preps.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prep'):
            PrepId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            PakQty.append(x.findtext('PakQty'))
            PakUOM.append(x.findtext('PakUOM'))
            InventoryGroup.append(x.findtext('InventoryGroup'))
    
Preps = pd.DataFrame({'PrepId': PrepId, 'Description': Description,
                  'PakQty': PakQty, 'PakUOM':PakUOM, 'InventoryGroup': InventoryGroup}).drop_duplicates()
preps_columns = Preps.columns
Preps.drop_duplicates(subset=["PrepId"], inplace=True)

Preps.reset_index(drop=True, inplace=True)

In [30]:
Preps

PrepId                     Description    PakQty PakUOM  \
0    P-41914       GRL|Grilled Chicken Thigh     2.000     Kg   
1    P-56387    BATCH| Szechuan Green Beans    500.000      g   
2    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
3    P-44438     BATCH|Garlic Bread|Baguette     1.000    PTN   
4    P-47958          BATCH|Greek Salad|BASE    10.000     Kg   
5    P-56398                 BATCH|Guacamole     2.500     Kg   
6    P-54677    BATCH|Marinated Tofu|GRILLED     6.800     Kg   
7    P-56766  BATCH|oven roasted tomatoes|MC     1.000     lb   
8    P-42354        BATCH|Pulled Pork Braise    36.000     Kg   
9    P-47654       BATCH|Vegetarian Furikake     2.310     Kg   
10   P-42364               BB|MexicanCabbage     1.000     Kg   
11   P-44335      BB|White Bean Burrito Base    10.400     Kg   
12   P-54692                BLANCHED|Spinach     3.000     Kg   
13   P-26636              BUTTER|Garlic Herb     1.905     Kg   
14   P-24750                CHOPPED|Cilantro     0.500     Kg   
15   P-26647           COOKED| Whole W Penne     9.072     Kg   
16   P-51214      COOKED|Ancho Chicken|Batch     8.000     Kg   
17   P-41574         COOKED|BlackBeans|Bueno    30.000      L   
18   P-47324         COOKED|Meatball Blended   180.000   each   
19   P-37297              COOKED|Poached Egg     1.000   each   
20   P-26959              COOKED|Rice Noodle    10.000     lb   
21   P-55452        COOKED|Shitake Mushrooms     2.000     Kg   
22   P-53979         COOKED|Veggie Chow Mein    25.000     Kg   
23   P-26884   COOKED|Whole Grain Brown Rice     4.000     Kg   
24   P-50411   COOKEDlNavy Bean (white bean)   415.000      g   
25   P-48863          DES|Brown Rice Pudding    12.000     CT   
26   P-55287       DESSERT|Chocolate Pudding     5.100      L   
27   P-41094               DICED|Carrot|1/4"    11.170     Kg   
28   P-50977                    DICED|Celery   850.000      g   
29   P-41095               DICED|Celery|1/4"    13.608     Kg   
30   P-43962             DICED|Cucumber|1/4"     3.300     Kg   
31   P-50839              DICED|Green Pepper   800.000      g   
32   P-50550                 DICED|Onion Red    23.000     lb   
33   P-50552              DICED|Onion Yellow    23.000     lb   
34   P-57499             DICED|Red Onion 1/8    11.000     Kg   
35   P-50837                DICED|Red Pepper   800.000      g   
36   P-44429          DICED|Roma Tomato|1/4"     1.000     Kg   
37   P-39167         DICED|Yellow Onion|3/4"    11.010     Kg   
38   P-45194             DICED|Zucchini|3/4"     1.000     Kg   
39   P-51531               DRAINED|Baby Corn     1.400     Kg   
40   P-54280               DRAINED|Pineapple     1.750     Kg   
41   P-35750          DRESSING|Spicy Caesar      4.400      L   
42   P-44311               Dressing|Tabouleh     1.400      L   
43   P-42160         DRESSING|Tahini Drizzle     1.500      L   
44   P-26054                 DRESSINGlCaesar     9.000      L   
45   P-42817                  FLEX|Aloo Gobi    27.000     Kg   
46   P-45624              FLEX|Beef Vindaloo    63.000     Kg   
47   P-55370           FLEX|Japchae Stir fry     5.000     Kg   
48   P-43658      FLEX|Mint Cilantro Chutney     1.000     Kg   
49   P-44410               FLEX|Palak Paneer    33.000     Kg   
50   P-44353              FLEX|Savoury Chaat     7.000    PTN   
51   P-51321    FLEX|Seafood Pancake Batter     20.000     Kg   
52   P-44083           FLEX|Tamarind Chutney     1.000      L   
53   P-55371              FLEX|Teriyaki Tofu     3.000     Kg   
54   P-27397             FLEXlVindaloo paste    15.000     Kg   
55   P-55776        FLX|Sauce|Cucumber Raita     6.000     Kg   
56   P-44363               FRIED|Cauliflower     6.000     Kg   
57   P-52042                      FRIED|Tofu     0.900     Kg   
58   P-50586                GARNISH|Cilantro   800.000      g   
59   P-50585             GARNISH|Green Onion   900.000      g   
60   P-52620     GARNISH|Lime Mini Wedge|

In [31]:
# This tells us that there are not any duplicates in the Preps dataframe. There is a different process|ingredient pair for 
# all the recipes. 
check = Preps["PrepId"].duplicated().any()
print(check)

False


In [32]:
# There are 546 rows and 5 columns
Preps.shape

(581, 5)

In [33]:
# Here we see there is only one place P-50739 is used in the Preps
Preps.loc[Preps["PrepId"] == "P-50739"]

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup]
Index: []

In [34]:
Preps.dtypes

PrepId            object
Description       object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [35]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Preps_List.csv")
Preps.to_csv(path, index = False, header = True)

### Import Products List

In [36]:
# Read products.xml files in the filepath_list and construct a dataframe
ProdId = []
Description = []
SalesGroup = []

# From the XML file for products append the id into ProdId, description into Description, and SalesGroup into SalesGroup list.
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe

for filepath in filepath_list:
    path = filepath + '/Products.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prod'):
            ProdId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            SalesGroup.append(x.findtext('SalesGroup'))
        
Products = pd.DataFrame({'ProdId': ProdId, 'Description': Description, 'SalesGroup': SalesGroup})
Products.drop_duplicates(inplace=True)

Products.reset_index(drop=True, inplace=True)

In [37]:
Products

ProdId                     Description            SalesGroup
0    R-55408                      ADD|Cheese               ADD ONS
1    R-22896                    ADD|Crackers               ADD ONS
2    R-53006        HS|ADD|Chicken Thigh (2)               ADD ONS
3    R-52751                 BAKE|Bagel Asst             FT BAKERY
4    R-19583             BAKE|Cake|Ponderosa             FT BAKERY
5    R-52747               BAKE|Cinnamon Bun             FT BAKERY
6    R-52742           BAKE|Croissant|Almond             FT BAKERY
7    R-52743           BAKE|Croissant|Cheese             FT BAKERY
8    R-52744        BAKE|Croissant|Chocolate             FT BAKERY
9    R-52745     BAKE|Croissant|Ham & Cheese             FT BAKERY
10   R-52741            BAKE|Croissant|Plain             FT BAKERY
11   R-52793  BAKE|Croissant|Spinach Pepper              FT BAKERY
12   R-52750      BAKE|Danish|Almond Pear|MC             FT BAKERY
13   R-52749        BAKE|Danish|Supreme Asst             FT BAKERY
14   R-21282            BAKE|Loaf|Sweet Asst             FT BAKERY
15   R-46225                BAKE|Muffin|Asst             FT BAKERY
16   R-20398                 BAKE|Scone|Asst             FT BAKERY
17   R-47788  BAKE|Scone|Cran & Blueberry|MC             FT BAKERY
18   R-54278     BLOWOUT|Crab Cakes w Ceasar                 FEAST
19   R-54277          BLOWOUT|MiniHotDog|GRL                 FEAST
20   R-54282                 BLOWOUT|PomPom                  FEAST
21   R-54283            BLOWOUT|Riblette S/W                 FEAST
22   R-54281      BLOWOUT|YamChikPatty w CZR                 FEAST
23   R-44315          BNO|Bowl|Ancho Chicken              FT BUENO
24   R-44308            BNO|Bowl|Pulled Pork              FT BUENO
25   R-44310                  BNO|Bowl|Steak              FT BUENO
26   R-51215             BNO|Bowl|White Bean              FT BUENO
27   R-43587       BNO|Burrito|Ancho Chicken              FT BUENO
28   R-44303         BNO|Burrito|Pulled Pork              FT BUENO
29   R-44316         BNO|Burrito|White Bean               FT BUENO
30   R-53127              BU|BOWL WHITE BEAN                 FEAST
31   R-52808            DES|Biscotti|MC|Asst           FT DESSERTS
32   R-47480          DES|Brownie|Black Bean           FT DESSERTS
33   R-52792                  DES|Brownie|MC           FT DESSERTS
34   R-22312    DES|Cake|Cheesecake|New York           FT DESSERTS
35   R-48241       DES|Cake|Rondine Tiramisu           FT DESSERTS
36   R-22310             DES|Cake|Slice Asst           FT DESSERTS
37   R-55145  DES|Cake|Valentine Choco Heart           FT DESSERTS
38   R-23333     DES|Cheesecake|Chuckanut|GF           FT DESSERTS
39   R-55289   DES|Chocolate Pudding Praline           FT DESSERTS
40   R-43301                      DES|Churro           FT DESSERTS
41   R-39459     DES|Cookie|Pumpkin Sugar|CK           FT DESSERTS
42   R-49713             DES|Cookie|Shamrock           FT DESSERTS
43   R-20399         DES|Cookie|Supreme Asst           FT DESSERTS
44   R-55070  DES|Cookie|Valentine Heart|Tru           FT DESSERTS
45   R-55069  DES|Cookie|Valentine Sandwich            FT DESSERTS
46   R-40508   DES|Cookie|Wendel's|Choc Chip           FT DESSERTS
47   R-40021      DES|Cookie|Wendel's|Ginger           FT DESSERTS
48   R-20381     DES|Cookie|Wendel's|Ginger.           FT DESSERTS
49   R-48895     DES|Cookie|Xmas|Ginger Bear           FT DESSERTS
50   R-33032   DES|Cookie|Xmas|Ginger People           FT DESSERTS
51   R-54261       DES|Cookie|Xmas|Snowflake           FT DESSERTS
52   R-54186       DES|Cookie|Xmas|Tree/Bell           FT DESSERTS
53   R-22313            DES|Eclair|Chocolate           FT DESSERTS
54   R-22309                  DES|Jello|Asst           FT DESSERTS
55   R-23335         DES|Muffin|Blueberry|GF           FT DESSERTS
56   R-53141   DES|Pie|Lemon Meringue|Slice            FT DESSERTS
57   R-22311              DES|Pie|Slice Asst           FT DESSERTS
58   R-48864         DES|Pudding|Brown Rice          

In [38]:
# Here we can see that there is only one R-56966 in the products 
Products.loc[Products["ProdId"] == "R-56966"]

Empty DataFrame
Columns: [ProdId, Description, SalesGroup]
Index: []

In [39]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [40]:
# Here we can see that there is only one R-68698 in the products 
Products.loc[Products["ProdId"] == "R-68698"]

Empty DataFrame
Columns: [ProdId, Description, SalesGroup]
Index: []

In [41]:
Products.shape

(501, 3)

In [42]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [43]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Products_List.csv")
Products.to_csv(path, index = False, header = True)

### Import Conversions List

In [44]:
# Read conventions.xml files in the filepath_list and construct a dataframe
ConversionId = []
Multiplier = []
ConvertFromQty = []
ConvertFromUom = []
ConvertToQty = []
ConvertToUom = []

# From the XML file for Conversions append the id into ConversionId, multiplier into Multiplier, ConvertFrom->qty into 
# ConvertFromQty,ConvertFrom->uom into ConvertFromUom, ConvertTo->qty into ConvertToQty and and ConvertTo->uom into the
# CovertToUom list. 
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe


for filepath in filepath_list:
    path = filepath + '/Conversions.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Conversion'):
            ConversionId.append(x.attrib['id'])
            Multiplier.append(x.attrib['multiplier'])
            ConvertFromQty.append(x.find('ConvertFrom').attrib['qty'])
            ConvertFromUom.append(x.find('ConvertFrom').attrib['uom'])
            ConvertToQty.append(x.find('ConvertTo').attrib['qty'])
            ConvertToUom.append(x.find('ConvertTo').attrib['uom'])
    
    
Conversions = pd.DataFrame({'ConversionId': ConversionId, 'Multiplier': Multiplier, 'ConvertFromQty': ConvertFromQty,
                           'ConvertFromUom': ConvertFromUom, 'ConvertToQty': ConvertToQty, 'ConvertToUom': ConvertToUom}
                          ).drop_duplicates()

Conversions.reset_index(drop=True, inplace=True)

In [45]:
# Here we can see for example that to convert 1.14 L to 1 L the multiplier is 0.877 since 1/1.14 = 0.877
Conversions

ConversionId     Multiplier ConvertFromQty ConvertFromUom ConvertToQty  \
0                    1.00000000         1.0000            XXX       1.0000   
1                    0.87719298         1.0000          1.14L       1.1400   
2                    0.66666667         1.0000           1.5L       1.5000   
3                    0.57142857         1.0000         1.75 L       1.7500   
4                    0.50000000         1.0000             2L       2.0000   
5                    0.25000000         1.0000             4L       4.0000   
6                    0.08333333         1.0000           FOOT      12.0000   
7                    0.06250000         1.0000            16L      16.0000   
8                    0.05917160         1.0000         1/2LTR      16.9000   
9                    0.03937008         1.0000          750ML      25.4000   
10                   0.03333333         1.0000        KEG 30L      30.0000   
11                   0.02597403         1.0000         1140ml      38.5000   
12                   0.02500000         1.0000        full in      40.0000   
13                   0.02000000         1.0000        KEG 50L      50.0000   
14                   0.01706485         1.0000        KEG 59L      58.6000   
15                   0.01666667         1.0000           HOUR      60.0000   
16                   0.00200000         1.0000          500ML     500.0000   
17                   0.00153846         1.0000          650ML     650.0000   
18                   0.00151515         1.0000          660ML     660.0000   
19                   0.00142857         1.0000          700ML     700.0000   
20                   0.00140845         1.0000          710ml     710.0000   
21                   0.00133333         1.0000          750ML     750.0000   
22                   0.00059172         1.0000         keg50L    1690.0000   
23                   0.00050403         1.0000         keg59L    1984.0000   
24                   2.00000000         2.0000            cup       1.0000   
25                   2.00000000         2.0000             pt       1.0000   
26                   2.00000000         2.0000           Tbsp       1.0000   
27                   3.00000000         3.0000            tsp       1.0000   
28                   4.00000000         4.0000             qt       1.0000   
29                   8.00000000         8.0000          fl oz       1.0000   
30                  16.00000000        16.0000             oz       1.0000   
31                  28.34950000        28.3495              g       1.0000   
32                  29.57350000        29.5735             ml       1.0000   
33                  35.21126761       100.0000          fl oz       2.8400   
34                1000.00000000      1000.0000              g       1.0000   
35                1000.00000000      1000.0000             mg       1.0000   
36                1000.00000000      1000.0000             ml       1.0000   
37        I-3237     0.16666667         1.0000            pak       6.0000   
38        I-3388     0.22222222         1.0000            tsp       4.5000   
39        I-3388     0.07142857         1.0000           Tbsp      14.0000   
40        I-3388     0.00458716         1.0000            cup     218.0000   
41        I-3642     0.14492754         1.0000           Tbsp       6.9000   
42        I-1197     0.01333333         1.0000             CT      75.0000   
43        I-1813     0.03278689         1.0000          fl oz      30.5000   
44        I-1813     0.00409836         1.0000            cup     244.0000   
45        I-1820     0.03215434         1.0000          fl oz      31.1000   
46        I-1820     0.00401606         1.0000            cup     249.0000   
47        I-1821     0.03194888         1.0000          fl oz      31.3000   
48        I-1821     0.00400000         1.0000            cup     250.0000   
49        I-2159     1.00000000         1.0000             CT       1.0000   
50        I-2159     0.030

In [46]:
# Here we can check that there are no ingredients listed since 
Conversions.loc[Conversions["ConversionId"] == "I-4582"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [47]:
all_id_list = Items["ItemId"].unique()
all_conv_list = Conversions["ConversionId"].unique()

print("All unique IDs list\n")
print(all_id_list)
print("\n")
print("All unique Conversions list\n")
print(all_conv_list)

All unique IDs list

['I-2110' 'I-4027' 'I-3237' 'I-3388' 'I-3642' 'I-6026' 'I-43851' 'I-3617'
 'I-43854' 'I-4472' 'I-4973' 'I-1252' 'I-1277' 'I-1286' 'I-8118' 'I-4497'
 'I-1402' 'I-1020' 'I-55475' 'I-62123' 'I-55476' 'I-3619' 'I-2567'
 'I-42273' 'I-23336' 'I-3143' 'I-4515' 'I-7935' 'I-3148' 'I-59287'
 'I-3837' 'I-10869' 'I-19711' 'I-47657' 'I-1157' 'I-45976' 'I-1283'
 'I-1016' 'I-46907' 'I-32395' 'I-32394' 'I-32393' 'I-38808' 'I-29427'
 'I-29443' 'I-29442' 'I-29441' 'I-29438' 'I-29437' 'I-29436' 'I-46611'
 'I-54182' 'I-29232' 'I-28697' 'I-8060' 'I-4550' 'I-4555' 'I-4558'
 'I-1050' 'I-1048' 'I-1060' 'I-1062' 'I-11804' 'I-12439' 'I-11824'
 'I-16216' 'I-1064' 'I-28412' 'I-11214' 'I-3620' 'I-4572' 'I-4574'
 'I-4593' 'I-3621' 'I-4601' 'I-4598' 'I-2122' 'I-14179' 'I-2141' 'I-2780'
 'I-1073' 'I-19665' 'I-44322' 'I-37477' 'I-41492' 'I-41491' 'I-5975'
 'I-3624' 'I-3625' 'I-5977' 'I-44472' 'I-15213' 'I-11215' 'I-3628'
 'I-1471' 'I-3223' 'I-3224' 'I-3225' 'I-3226' 'I-1389' 'I-1391' 'I-49595'
 'I

In [48]:
# Here we have the number of items in the list that are a part of the "all_id_list" but not part of the "all_conv_list"
missing_conv_id = []

for item in all_id_list:
    if item not in all_conv_list:
        missing_conv_id.append(item)
        
missing_conv_id
print(len(missing_conv_id))

727


In [49]:
Conversions.shape

(339, 6)

In [50]:
Conversions.loc[Conversions["ConversionId"] == "I-29389"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [51]:
Conversions.dtypes

ConversionId      object
Multiplier        object
ConvertFromQty    object
ConvertFromUom    object
ConvertToQty      object
ConvertToUom      object
dtype: object

In [52]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Conversions_List.csv")
Conversions.to_csv(path, index = False, header = True)

***
## Data Summary

In [53]:
# Summary of raw data imported for evaluation
# Here we have a summary of the number of items, preps, ingredients, products, conversions

datasum = pd.DataFrame([Items.shape, Preps.shape, Ingredients.shape, Products.shape, Conversions.shape],
                       columns = ['count', 'columns'], 
                       index = ['Items', 'Preps', 'Ingredients', 'Products', 'Conversions'])
datasum

count  columns
Items          913        7
Preps          581        5
Ingredients   3760        6
Products       501        3
Conversions    339        6